In [2]:
%pip install "duckdb==0.9.2" "quackosm==0.4.4" "magic-duckdb @ git+https://github.com/iqmo-org/magic_duckdb.git@f7b9f15c2bcb72ae14a2aa25fa43ac15ade937d8"

  Cloning https://github.com/iqmo-org/magic_duckdb.git (to revision f7b9f15c2bcb72ae14a2aa25fa43ac15ade937d8) to /tmp/pip-install-bojos6of/magic-duckdb_91dd21058ed74d6baf05ba893af4b432
  Running command git clone --filter=blob:none --quiet https://github.com/iqmo-org/magic_duckdb.git /tmp/pip-install-bojos6of/magic-duckdb_91dd21058ed74d6baf05ba893af4b432
  Running command git rev-parse -q --verify 'sha^f7b9f15c2bcb72ae14a2aa25fa43ac15ade937d8'
  Running command git fetch -q https://github.com/iqmo-org/magic_duckdb.git f7b9f15c2bcb72ae14a2aa25fa43ac15ade937d8
  Running command git checkout -q f7b9f15c2bcb72ae14a2aa25fa43ac15ade937d8
  Resolved https://github.com/iqmo-org/magic_duckdb.git to commit f7b9f15c2bcb72ae14a2aa25fa43ac15ade937d8
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 121.4/121.4 kB 2.1 MB/s eta 0:00:00a 0:00:01
  Installing build dependenc

In [3]:
import geopandas as gpd

### Setup DuckDB connection and load `spatial` extension

In [4]:
%load_ext magic_duckdb

In [5]:
%%dql
INSTALL spatial;
LOAD spatial;

Empty DataFrame
Columns: [Success]
Index: []

In [6]:
con = %dql --getcon

# Reading OSM data

## File metadata

In [7]:
%%dql -t show
DESCRIBE SELECT * FROM ST_READOSM('monaco-latest.osm.pbf')

┌─────────────┬──────────────────────────────────────────────┬─────────┬─────────┬─────────┬─────────┐
│ column_name │                 column_type                  │  null   │   key   │ default │  extra  │
│   varchar   │                   varchar                    │ varchar │ varchar │ varchar │ varchar │
├─────────────┼──────────────────────────────────────────────┼─────────┼─────────┼─────────┼─────────┤
│ kind        │ ENUM('node', 'way', 'relation', 'changeset') │ YES     │ NULL    │ NULL    │ NULL    │
│ id          │ BIGINT                                       │ YES     │ NULL    │ NULL    │ NULL    │
│ tags        │ MAP(VARCHAR, VARCHAR)                        │ YES     │ NULL    │ NULL    │ NULL    │
│ refs        │ BIGINT[]                                     │ YES     │ NULL    │ NULL    │ NULL    │
│ lat         │ DOUBLE                                       │ YES     │ NULL    │ NULL    │ NULL    │
│ lon         │ DOUBLE                                       │ YES     │ 

## Count elements

In [8]:
%%dql -t show
SELECT COUNT(*) as total_elements
FROM ST_READOSM('monaco-latest.osm.pbf')

┌────────────────┐
│ total_elements │
│     int64      │
├────────────────┤
│          35782 │
└────────────────┘



In [9]:
%%dql -t show
SELECT kind, COUNT(*) as total_features
FROM ST_READOSM('monaco-latest.osm.pbf')
GROUP BY 1

┌──────────────────────────────────────────────┬────────────────┐
│                     kind                     │ total_features │
│ enum('node', 'way', 'relation', 'changeset') │     int64      │
├──────────────────────────────────────────────┼────────────────┤
│ node                                         │          30643 │
│ way                                          │           4849 │
│ relation                                     │            290 │
└──────────────────────────────────────────────┴────────────────┘



## See examples of the data

In [19]:
%%dql -t show -tp max_width 160
SELECT *
FROM ST_READOSM('monaco-latest.osm.pbf')
WHERE kind = 'node'
LIMIT 5

┌──────────────────────┬──────────┬────────────────────────┬─────────┬────────────────────┬────────────────────┬───────────┬───────────────────────────────────┐
│         kind         │    id    │          tags          │  refs   │        lat         │        lon         │ ref_roles │             ref_types             │
│ enum('node', 'way'…  │  int64   │ map(varchar, varchar)  │ int64[] │       double       │       double       │ varchar[] │ enum('node', 'way', 'relation')[] │
├──────────────────────┼──────────┼────────────────────────┼─────────┼────────────────────┼────────────────────┼───────────┼───────────────────────────────────┤
│ node                 │ 21911883 │ NULL                   │ NULL    │ 43.737117500000004 │  7.422909300000001 │ NULL      │ NULL                              │
│ node                 │ 21911886 │ {crossing=zebra, cro…  │ NULL    │ 43.737239900000006 │  7.423498500000001 │ NULL      │ NULL                              │
│ node                 │ 21911894 

In [22]:
%%dql -t show -tp max_width 160
SELECT *
FROM ST_READOSM('monaco-latest.osm.pbf')
WHERE kind = 'way'
LIMIT 5

┌──────────────────────┬─────────┬──────────────────────┬────────────────────────────────────┬────────┬────────┬───────────┬───────────────────────────────────┐
│         kind         │   id    │         tags         │                refs                │  lat   │  lon   │ ref_roles │             ref_types             │
│ enum('node', 'way'…  │  int64  │ map(varchar, varch…  │              int64[]               │ double │ double │ varchar[] │ enum('node', 'way', 'relation')[] │
├──────────────────────┼─────────┼──────────────────────┼────────────────────────────────────┼────────┼────────┼───────────┼───────────────────────────────────┤
│ way                  │ 4097656 │ {highway=secondary…  │ [21912089, 7265761724, 107975074…  │   NULL │   NULL │ NULL      │ NULL                              │
│ way                  │ 4098197 │ {highway=tertiary,…  │ [21918500, 10723812919, 12042884…  │   NULL │   NULL │ NULL      │ NULL                              │
│ way                  │ 4224972 │

In [23]:
%%dql -t show -tp max_width 160
SELECT *
FROM ST_READOSM('monaco-latest.osm.pbf')
WHERE kind = 'relation'
LIMIT 5

┌──────────────────────┬───────┬──────────────────────┬──────────────────────┬────────┬────────┬──────────────────────┬────────────────────────────────────────┐
│         kind         │  id   │         tags         │         refs         │  lat   │  lon   │      ref_roles       │               ref_types                │
│ enum('node', 'way'…  │ int64 │ map(varchar, varch…  │       int64[]        │ double │ double │      varchar[]       │   enum('node', 'way', 'relation')[]    │
├──────────────────────┼───────┼──────────────────────┼──────────────────────┼────────┼────────┼──────────────────────┼────────────────────────────────────────┤
│ relation             │  7385 │ {ISO3166-2=FR-06, …  │ [1701090139, 32665…  │   NULL │   NULL │ [admin_centre, lab…  │ [node, node, way, way, way, way, way…  │
│ relation             │  8654 │ {ISO3166-2=FR-PAC,…  │ [26761400, 1251610…  │   NULL │   NULL │ [admin_centre, lab…  │ [node, node, way, way, way, way, way…  │
│ relation             │ 11980 │ {

## Extracting the geometries

### Nodes

In [25]:
%%dql -t show
SELECT
    id,
    tags,
    ST_POINT(lon, lat) geometry
FROM ST_READOSM('monaco-latest.osm.pbf')
WHERE kind = 'node'
    AND tags IS NOT NULL
    AND cardinality(tags) > 0;

┌─────────────┬─────────────────────────────────────────────────────────────────────────────────────────────────┬──────────────────────────────────────────────┐
│     id      │                                              tags                                               │                   geometry                   │
│    int64    │                                      map(varchar, varchar)                                      │                   geometry                   │
├─────────────┼─────────────────────────────────────────────────────────────────────────────────────────────────┼──────────────────────────────────────────────┤
│    21911886 │ {crossing=zebra, crossing:island=no, crossing_ref=zebra, highway=crossing}                      │ POINT (7.423498500000001 43.737239900000006) │
│    21912962 │ {crossing=zebra, crossing_ref=zebra, highway=crossing}                                          │ POINT (7.426912100000001 43.737912800000004) │
│    21914341 │ {crossing=uncontro

In [26]:
gpd.GeoSeries.from_wkt(
    con.sql("""
        SELECT ST_AsText(ST_POINT(lon, lat)) wkt
        FROM ST_READOSM('monaco-latest.osm.pbf')
        WHERE kind = 'node' AND tags IS NOT NULL AND cardinality(tags) > 0;
    """).df()['wkt'],
    crs='EPSG:4326'
).explore(tiles="CartoDB positron") #.save('monaco_points.html')

### Ways

In [27]:
%%dql -t show
CREATE OR REPLACE TEMP TABLE matching_ways AS 
SELECT id, tags
FROM ST_READOSM('monaco-latest.osm.pbf')
WHERE kind = 'way' AND tags IS NOT NULL AND cardinality(tags) > 0;

SELECT * FROM matching_ways;

┌────────────┬─────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────┐
│     id     │                                                                      tags                                                                       │
│   int64    │                                                              map(varchar, varchar)                                                              │
├────────────┼─────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────┤
│    4097656 │ {highway=secondary, lanes=2, lit=yes, maxspeed=30, name=Avenue Princesse Alice, surface=asphalt}                                                │
│    4098197 │ {highway=tertiary, lanes=2, lit=yes, name=Boulevard d'Italie, smoothness=excellent, surface=asphalt}                                            │
│    4224972 │ {highway=residentia

In [28]:
%%dql -t show
CREATE OR REPLACE TEMP TABLE matching_ways_with_nodes_refs AS
SELECT id, UNNEST(refs) as ref, UNNEST(range(length(refs))) as ref_idx
FROM ST_READOSM('monaco-latest.osm.pbf')
WHERE kind = 'way' AND tags IS NOT NULL AND cardinality(tags) > 0;

SELECT * FROM matching_ways_with_nodes_refs;

┌───────────┬────────────┬─────────┐
│    id     │    ref     │ ref_idx │
│   int64   │   int64    │  int64  │
├───────────┼────────────┼─────────┤
│   4097656 │   21912089 │       0 │
│   4097656 │ 7265761724 │       1 │
│   4097656 │ 1079750744 │       2 │
│   4097656 │ 2104793864 │       3 │
│   4097656 │ 6340961560 │       4 │
│   4097656 │ 1110560507 │       5 │
│   4097656 │   21912093 │       6 │
│   4097656 │ 6340961559 │       7 │
│   4097656 │   21912095 │       8 │
│   4097656 │ 7265762803 │       9 │
│      ·    │      ·     │       · │
│      ·    │      ·     │       · │
│      ·    │      ·     │       · │
│ 151154357 │ 7927855820 │       2 │
│ 151154358 │ 1868015912 │       0 │
│ 151154358 │ 1868015910 │       1 │
│ 151154358 │ 1868015900 │       2 │
│ 151154358 │ 4437858221 │       3 │
│ 151154358 │ 1868015889 │       4 │
│ 151154358 │ 1790048390 │       5 │
│ 151154358 │ 1868015881 │       6 │
│ 151154358 │ 1868015894 │       7 │
│ 151154358 │ 1868015896 │       8 │
├

In [29]:
%%dql -t show
CREATE OR REPLACE TEMP TABLE required_nodes_with_geometries AS
SELECT id, ST_POINT(lon, lat) geometry
FROM ST_READOSM('monaco-latest.osm.pbf') nodes
SEMI JOIN matching_ways_with_nodes_refs ON nodes.id = matching_ways_with_nodes_refs.ref
WHERE kind = 'node';

SELECT * FROM required_nodes_with_geometries;

┌────────────┬──────────────────────────────────────────────┐
│     id     │                   geometry                   │
│   int64    │                   geometry                   │
├────────────┼──────────────────────────────────────────────┤
│ 4547239708 │ POINT (7.4219302 43.7307441)                 │
│ 4547239709 │ POINT (7.421943700000001 43.730763)          │
│ 4547239710 │ POINT (7.421885100000001 43.7308797)         │
│ 4547239711 │ POINT (7.421869 43.730828200000005)          │
│ 4547239712 │ POINT (7.4218596 43.7307865)                 │
│ 4547239713 │ POINT (7.4219166 43.7307701)                 │
│ 4547239714 │ POINT (7.4220242 43.730742)                  │
│ 4547239715 │ POINT (7.4220765 43.730725500000005)         │
│ 4547239716 │ POINT (7.4220677 43.730680400000004)         │
│ 4547239717 │ POINT (7.422105200000001 43.730662)          │
│      ·     │                  ·                           │
│      ·     │                  ·                           │
│      ·

In [30]:
%%dql -t show
CREATE OR REPLACE TEMP TABLE matching_ways_linestrings AS
SELECT
    matching_ways.id,
    matching_ways.tags,
    ST_MakeLine(list(nodes.geometry ORDER BY ref_idx ASC)) linestring
FROM matching_ways
JOIN matching_ways_with_nodes_refs
ON matching_ways.id = matching_ways_with_nodes_refs.id
JOIN required_nodes_with_geometries nodes
ON matching_ways_with_nodes_refs.ref = nodes.id
GROUP BY 1, 2;

SELECT * FROM matching_ways_linestrings;

┌────────────┬──────────────────────┬──────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────┐
│     id     │         tags         │                                                        linestring                                                        │
│   int64    │ map(varchar, varch…  │                                                         geometry                                                         │
├────────────┼──────────────────────┼──────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────┤
│    4227212 │ {highway=residenti…  │ LINESTRING (7.424979 43.731506200000005, 7.4249447 43.731479500000006, 7.4249412 43.731445, 7.424980100000001 43.73142…  │
│    4227230 │ {access=yes, admin…  │ LINESTRING (7.4220576 43.7321018, 7.4221642 43.732117900000006, 7.4222714 43.7321316, 7.422379100000001 43.7321425)      │
│    4227273 │ {highway=secondary…

In [31]:
gpd.GeoSeries.from_wkt(
    con.sql("""
        SELECT ST_AsText(linestring) wkt
        FROM matching_ways_linestrings
    """).df()["wkt"],
    crs="EPSG:4326",
).explore(
    tiles="CartoDB positron", style_kwdsdict=dict(weight=1)
) #.save("monaco_ways_linestrings.html")

In [32]:
%%dql -t show
WITH way_polygon_feature AS (
    SELECT
        id,
        (
            -- if first and last nodes are the same
            ST_Equals(ST_StartPoint(linestring), ST_EndPoint(linestring))
            -- if the element doesn't have any tags leave it as a Linestring
            AND tags IS NOT NULL
            -- if the element is specifically tagged 'area':'no' -> LineString
            AND NOT (
                list_contains(map_keys(tags), 'area')
                AND list_extract(map_extract(tags, 'area'), 1) = 'no'
            )
        ) AS is_polygon
    FROM matching_ways_linestrings
)
SELECT
    matching_ways_linestrings.id,
    matching_ways_linestrings.tags,
    (CASE
        WHEN is_polygon
        THEN ST_MakePolygon(linestring)
        ELSE linestring
    END)::GEOMETRY AS geometry
FROM matching_ways_linestrings
JOIN way_polygon_feature
ON matching_ways_linestrings.id = way_polygon_feature.id;

┌────────────┬──────────────────────┬──────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────┐
│     id     │         tags         │                                                         geometry                                                         │
│   int64    │ map(varchar, varch…  │                                                         geometry                                                         │
├────────────┼──────────────────────┼──────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────┤
│    4227212 │ {highway=residenti…  │ LINESTRING (7.424979 43.731506200000005, 7.4249447 43.731479500000006, 7.4249412 43.731445, 7.424980100000001 43.73142…  │
│    4227230 │ {access=yes, admin…  │ LINESTRING (7.4220576 43.7321018, 7.4221642 43.732117900000006, 7.4222714 43.7321316, 7.422379100000001 43.7321425)      │
│    4227273 │ {highway=secondary…

In [33]:
gpd.GeoSeries.from_wkt(
    con.sql("""
        WITH way_polygon_feature AS (
            SELECT
                id,
                (
                    ST_Equals(ST_StartPoint(linestring), ST_EndPoint(linestring))
                    AND tags IS NOT NULL
                    AND NOT (
                        list_contains(map_keys(tags), 'area')
                        AND list_extract(map_extract(tags, 'area'), 1) = 'no'
                    )
                ) AS is_polygon
            FROM matching_ways_linestrings
        )
        SELECT
            ST_AsText((CASE
                WHEN is_polygon
                THEN ST_MakePolygon(linestring)
                ELSE linestring
            END)) AS wkt
        FROM matching_ways_linestrings
        JOIN way_polygon_feature
        ON matching_ways_linestrings.id = way_polygon_feature.id;
    """).df()["wkt"],
    crs="EPSG:4326",
).explore(
    tiles="CartoDB positron", style_kwdsdict=dict(weight=1)
) #.save("monaco_ways_geometries.html")